## Assignment 2.1

**Joris LIMONIER**


$\mathbf{Exercise\, 1.}$ Illustrate with a meaningful example the bias variance decomposition, as we have seen it during lesson, for the non linear Support Vector Regression model, for increasing vaues of the regularization parameter _C_ (for example C = 1e-3, 1e-2, 1e-1, 1, 1e2, $\ldots$).


In [1]:
# data
import numpy as np
import pandas as pd

# sklearn
from sklearn.svm import SVR

# plotting
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots


In [2]:
## sklearn call for Support Vector Regression with C = parameter_value
C_exp_min = -5
C_exp_max = 5

err_mess = f"minimum exponent of C must be less than maximum exponent of C"
assert C_exp_min < C_exp_max, err_mess

# make list of values of C as powers of 10
C_val = np.array([10 ** k for k in range(C_exp_min, C_exp_max)])

noise_level = 1
C = 1e-4
n_samples = 100
range_min = -3
range_max = 3
noise_level = 5
ground_truth_func = lambda x: 0.5 * np.sin(2 * x) - (x / 20)


def generate_synth_data(
    n_samples,
    range_min,
    range_max,
    noise_level,
    ground_truth_func,
):
    """
    generate `n_samples` of synthetic data between `range_min` and `range_max`,
    with some noise, based on a `ground_truth_func` function
    """

    X = np.linspace(start=range_min, stop=range_max, num=n_samples)
    noise = noise_level * np.random.randn(n_samples)

    return X.reshape(-1, 1), ground_truth_func(X) + noise


X, y = generate_synth_data(
    n_samples=n_samples,
    range_min=range_min,
    range_max=range_max,
    noise_level=noise_level,
    ground_truth_func=ground_truth_func,
)
px.scatter(x=X[:, 0], y=y)


In [3]:
def plot_pred(
    C,
    n_samples,
    range_min,
    range_max,
    noise_level,
    ground_truth_func,
    return_bias_var=False,
):
    """
    plot predictions and their mean
    """

    all_bias = np.array([])
    all_var = np.array([])

    predictions = np.array([])
    fig = px.scatter(title=f"C value {C}")
    for i in range(42):
        X, y = generate_synth_data(
            n_samples, range_min, range_max, noise_level, ground_truth_func
        )
        model = SVR(kernel="rbf", C=C)
        model.fit(X, y)
        y_pred = model.predict(X)
        predictions = np.append(arr=predictions, values=y_pred)

        trace = go.Scatter(
            x=X[:, 0],
            y=predictions.reshape(-1, len(y_pred))[i],
            name=f"predictions{i}",
            opacity=0.05,
            marker={"color": "blue"},
        )
        fig.add_trace(trace=trace)

    # reshape predictions in stacks of y_pred's
    predictions = predictions.reshape(-1, len(y_pred))
    mean_pred = np.mean(a=predictions, axis=0)

    # store bias
    bias = np.sum((ground_truth_func(X) - mean_pred.reshape(-1, 1)) ** 2, axis=0)
    all_bias = np.append(arr=all_bias, values=bias)
    # store variance
    var_pred = np.var(predictions, axis=0)
    variance = np.sum(var_pred)
    all_var = np.append(arr=all_var, values=variance)

    # plot ground truth
    lin_space = np.linspace(range_min, range_max, n_samples)

    trace = go.Scatter(
        x=lin_space,
        y=mean_pred,
        name="mean pred",
        marker={"color": "black"},
        opacity=0.5,
    )
    fig.add_trace(trace=trace)

    X, y = generate_synth_data(
        n_samples, range_min, range_max, noise_level, ground_truth_func
    )
    trace = go.Scatter(
        x=X[:, 0],
        y=y,
        mode="markers",
        marker={"color": "red"},
    )
    fig.add_trace(trace=trace)

    fig.update_traces(showlegend=False)
    if return_bias_var:
        return fig, all_bias, all_var
    return fig


def join_plots(C_val, n_samples, range_min, range_max, noise_level, ground_truth_func):
    """
    Join plots with multiple values of C
    """
    subplot_titles = [f"Value of C: {C}" for C in C_val]

    fig = make_subplots(
        rows=(len(C_val) // 2) + 1, cols=2, subplot_titles=subplot_titles
    )

    for i, C in enumerate(C_val):
        traces = plot_pred(
            C, n_samples, range_min, range_max, noise_level, ground_truth_func
        ).data
        for trace in traces:
            fig.append_trace(trace, row=(i // 2) + 1, col=(i % 2) + 1)

    fig.update_layout(
        height=1500,
        title_text="Multiple Subplots with Titles",
    )

    return fig


In [4]:
join_plots(
    C_val,
    n_samples,
    range_min,
    range_max,
    noise_level,
    ground_truth_func,
)


$\mathbf{Exercise\, 2.}$ Modify the example of Exercise 1 to show the effect of increasing noise values on the bias and on the variance.


In [5]:
def bv_decomp(
    C=C,
    noise_level=noise_level,
    n_samples=n_samples,
    range_min=range_min,
    range_max=range_max,
    ground_truth_func=ground_truth_func,
    return_bias_var=True,
):
    """
    plot the the bias-variance decomposition
    """
    all_bias = np.array([])
    all_var = np.array([])

    for C in C_val:
        _, bias, var = plot_pred(
            C=C,
            n_samples=n_samples,
            range_min=range_min,
            range_max=range_max,
            noise_level=noise_level,
            ground_truth_func=ground_truth_func,
            return_bias_var=True,
        )
        all_bias = np.append(all_bias, bias)
        all_var = np.append(all_var, var)
    df_bias_var = pd.DataFrame(
        {"bias": all_bias, "var": all_var, "bias + var": all_bias + all_var},
        index=C_val,
    )
    return px.line(df_bias_var, title=f"noise level: {noise_level}", log_x=True)


In [6]:
for nl in range(1, 4):
    bv_decomp(noise_level=nl).show()


The bias + variance seems to perform best for `C` values of 0.1 or 1, depending on the noise and on the cell runs.

An increasing noise brings the variance to higher levels, but on our examples, it doesn't seem to fundamentally change the `C`-value for which the $bias + var$ is minimum.

---


$\mathbf{Exercise\, 3.}$ Still from the example of Exercise 1, compute the difference between training error and testing error for different vaues of the regularization parameter _C_.


In [7]:
def train_test_err_comp(
    n_samples=n_samples,
    range_min=range_min,
    range_max=range_max,
    noise_level=noise_level,
    ground_truth_func=ground_truth_func,
    samples_drawn=42,
):

    train_err = np.array([])
    test_err = np.array([])

    for C in C_val:
        for i in range(samples_drawn):
            # generate data
            X_train, y_train = generate_synth_data(
                n_samples=n_samples,
                range_min=range_min,
                range_max=range_max,
                noise_level=noise_level,
                ground_truth_func=ground_truth_func,
            )
            X_test, y_test = generate_synth_data(
                n_samples=n_samples,
                range_min=range_min,
                range_max=range_max,
                noise_level=noise_level,
                ground_truth_func=ground_truth_func,
            )

            # fit model
            model = SVR(kernel="rbf", C=C)
            model.fit(X_train, y_train)

            # predict
            y_pred_train = model.predict(X_train)
            y_pred_test = model.predict(X_test)

            # compute error on the current batch
            curr_train_err = np.mean((y_train - y_pred_train) ** 2)
            curr_test_err = np.mean((y_test - y_pred_test) ** 2)

            # store error
            train_err = np.append(train_err, curr_train_err)
            test_err = np.append(test_err, curr_test_err)

    # compute mean error for a given C on train
    train_err = train_err.reshape(-1, samples_drawn)
    train_err = np.mean(train_err, axis=1)

    # compute mean error for a given C on test
    test_err = test_err.reshape(-1, samples_drawn)
    test_err = np.mean(test_err, axis=1)

    return train_err, test_err


train_err, test_err = train_test_err_comp(
    n_samples=n_samples,
    range_min=range_min,
    range_max=range_max,
    noise_level=noise_level,
    ground_truth_func=ground_truth_func,
    samples_drawn=200,
)
train_err


array([25.02443353, 25.28827759, 24.88240608, 25.01757373, 24.62530814,
       24.38707431, 23.89422153, 23.70612767, 24.18290258, 23.34480676])

In [8]:
df_err_comp = pd.DataFrame(
    {"train_err": train_err, "test_err": test_err},
    index=C_val,
)
px.line(df_err_comp, log_x=True)


We see that the train error continuously decreases, whereas the test error stops decreasing after `C=0.01` (the C value after which test error increases is fairly unstable on re-runs, so may change if you re-run the cell).


## Assignment 2.2


We go back to the usual iris dataset


In [9]:
import numpy as np
import matplotlib.pyplot as plt

# importing the data from sklearn
from sklearn.datasets import load_iris

# importing the data from sklearn
from sklearn.datasets import load_iris

iris_dataset = load_iris()

# extracting the relevant information
data = iris_dataset.data
data_feature_names = iris_dataset.feature_names
target = iris_dataset.target
target_names = iris_dataset.target_names


$\mathbf{Exercise\, 1.}$ Using bootstrap, compute a 95% confidence interval for the median of the feature $\text{sepal length (cm)}$


In [10]:
alpha = 0.05
n_boot_rep = 42
conf_level = alpha / 2 * n_boot_rep

iris_df = pd.DataFrame(data, columns=data_feature_names)
iris_df


sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)
0                  5.1               3.5                1.4               0.2
1                  4.9               3.0                1.4               0.2
2                  4.7               3.2                1.3               0.2
3                  4.6               3.1                1.5               0.2
4                  5.0               3.6                1.4               0.2
..                 ...               ...                ...               ...
145                6.7               3.0                5.2               2.3
146                6.3               2.5                5.0               1.9
147                6.5               3.0                5.2               2.0
148                6.2               3.4                5.4               2.3
149                5.9               3.0                5.1               1.8

[150 rows x 4 columns]

In [11]:
def generate_boot(data, n_reps):
    """
    Generates `n_reps` bootstrapped samples from the `data` dataset.
    """
    boot = np.random.choice(data, size=(len(data), n_reps), replace=True)
    return boot


def confidence_interval(boot_estimator, repetitions, conf_level, estimator_name):
    """
    Calculates a confidence interval for a given bootstrapped estimator
    """

    # Calculating lower and upper bounds of the confidence interval
    low = np.sort(boot_estimator)[int(conf_level)]
    up = np.sort(boot_estimator)[int(repetitions - conf_level)]

    print(
        f"The {100-alpha}% confidence interval for the {estimator_name} is:",
        f"[{round(low, ndigits=4)}, {round(up, ndigits=4)}]",
    )
    return low, up


In [12]:
# Bootstrapping dataset

boot_data = generate_boot(
    data=iris_df["sepal length (cm)"],
    n_reps=n_boot_rep,
)
boot_median = np.median(boot_data, axis=0)
px.box(pd.Series(boot_median, name="median"))


In [13]:
confidence_interval(
    boot_estimator=boot_median,
    repetitions=n_boot_rep,
    conf_level=conf_level,
    estimator_name="median",
)


The 99.95% confidence interval for the median is: [5.6, 6.0]


(5.6, 6.0)

$\mathbf{Exercise\, 2.}$ Compute the null distribution for the hypothesis $H_0$: the mean of $\text{'sepal width (cm)'}$ is the same for $\text{setosa}$ and $\text{virginica}$.


In [14]:
n_reps = 2000
iris_df["target"] = target

# determine id of species
idx_setosa = np.argwhere(target_names == "setosa")[0, 0]
idx_virgin = np.argwhere(target_names == "virginica")[0, 0]

# filter by species
setosa = iris_df[iris_df["target"] == idx_setosa]["sepal width (cm)"]
virgin = iris_df[iris_df["target"] == idx_virgin]["sepal width (cm)"]


In [15]:
def compute_t(x, y):
    """
    Computes the t-statistic
    """
    # Compute mean
    mean_x = np.mean(x)
    mean_y = np.mean(y)

    # Compute var
    sigma2_x = np.var(x)
    sigma2_y = np.var(y)

    return (mean_x - mean_y) / np.sqrt(sigma2_x / len(x) + sigma2_y / len(y))


def center_concat_data(x, y):
    """
    Computes the centered data of the x and y distributions
    """

    # Center with respect to the concatenation of both distributions
    z = np.concatenate([x, y])
    mean_x = np.mean(x)
    mean_y = np.mean(y)

    # Translate the data with respect to the mean of z
    x_tilde = x - mean_x + np.mean(z)
    y_tilde = y - mean_y + np.mean(z)

    return x_tilde, y_tilde


def compute_t_boot(x, y, n_reps):
    """
    Computes the bootstrapped t statistics for two distributions x and y
    """

    t_boot = []

    # Computate centered x and y
    x_tilde, y_tilde = center_concat_data(x, y)

    # Generate B bootstrapped samples from concatenation of centered x and y
    z_tilde = np.concatenate([x_tilde, y_tilde])
    boot_samples = np.random.choice(
        a=z_tilde,
        size=(n_reps, len(x) + len(y)),
        replace=True,
    )

    # compute the t statistic for each bootstrapped sample
    for i in range(n_reps):
        x_sim = boot_samples[i, : len(x)]  # first len(x) samples of i-th boot replicate
        y_sim = boot_samples[i, len(x) :]  # the rest of the i-th boot replicate
        t_boot.append(compute_t(x_sim, y_sim))
    return t_boot


def plot_null_distr(t_obs, t_boot):
    """
    Plots the null hypothesis distribution
    """
    fig = px.histogram(pd.Series(t_boot, name="Null distribution"))
    fig.add_vline(
        x=t_obs,
        line_dash="dot",
        annotation_text="Observed t",
        annotation_position="top",
        annotation_font_size=20,
        annotation_font_color="black",
    )
    fig.update_layout(showlegend=True)
    fig.show()


In [16]:
# Compute observed t-statistic and bootstrapped-t statistic
t_obs = compute_t(setosa, virgin)
t_boot = compute_t_boot(
    x=setosa,
    y=virgin,
    n_reps=n_reps,
)
plot_null_distr(t_obs, t_boot)


$\mathbf{Exercise\, 3.}$ Compute a 2-sided bootstrapped p-value for the difference between the means of $\text{setosa}$ and $\text{virginica}$.


In [17]:
def test_hypothesis(t_obs, t_boot, repetitions):
    """
    Compare an observed t and compute its bootstrap.
    Then, adequately accept or reject an hypothesis
    """
    # Computes test significance
    boot_stat = np.sum(np.abs(t_obs) > np.abs(t_boot)) / repetitions
    confidence_interval = np.quantile(a=t_boot, q=[0.025, 0.975])
    print(
        f"Observed t statistic: {np.round(t_obs, 4)}",
        f"95% confidence interval: {np.round(confidence_interval, 4)}",
        f"Significance of the test: {np.round(boot_stat, 4)}",
        sep="\n",
    )


test_hypothesis(t_obs, t_boot, n_reps)


Observed t statistic: 6.5158
95% confidence interval: [-1.989   1.9501]
Significance of the test: 1.0


The observed t-value does not lie within the 95\% confidence interval, so we have to reject the null hypothesis. This means that the mean of the "sepal width (cm)" feature is different between setosa and virginica.
___


$\mathbf{Exercise\, 4.}$ The central limit theorem (Lindeberg-Levy version) states that given a sequence $X_1, X_2, \ldots, X_n $ of independent variables drawn from the same ditribution, $X_i\sim F$, then:

$$ \sqrt{n} \left( \frac{1}{n} \sum X_i - \mu \right) \rightarrow \mathcal{N}(0,\sigma^2),$$

where $\mu = \mathbf{E}[F]$ and $\sigma^2 = Var(F)$.
In particular, the sample mean converges to the normal distribution:

$$ \frac{1}{n} \sum X_i \rightarrow \mathcal{N}(\mu,\frac{\sigma^2}{n}). $$

Let $F = Exponential(2)$ be the exponential distribution with parameter $\lambda = 2$, and let $X_1, X_2, \ldots, X_{20}$ be 20 samples from this distribution. Verify for this case the central limit theorem via bootstrapping.

**\*\*** Remember, the mean of the exponential distribution is $\mathbf{E}(F) = 1/\lambda$, while the variance is $Var(F) = 1/\lambda^2$ **\*\***

Hint:

- Draw n samples (n large) from the Exponential distribution (be careful, when using $\text{np.random.exponential}$ the required input scale parameter is $\frac{1}{\lambda}$).
- Compute their average $\frac{\sum X_i}{20}$ and store the result


In [18]:
LAMBDA = 2
n_samples = 20
n_large = 10000

In [19]:
def boot_from_exp(lamb, n_samples, n_reps):
    """
    Generate bootstrapped samples from the Exponential distribution
    """
    boot = []
    for _ in range(n_reps):
        boot.append(np.random.exponential(1 / lamb, n_samples))
    return boot


def normal_from_exp(lamb, n_samples, n_reps):
    """
    Sample from a normal distribution with the same mean
    and standard deviation as the exponential distribution.
    """
    scale = 1 / lamb
    std = np.sqrt(scale ** 2 / n_samples)
    return np.random.normal(scale, std, n_reps)


In [20]:
# Compute mean of bootstrap samples
boot_samples = boot_from_exp(lamb=LAMBDA, n_samples=n_samples, n_reps=n_large)
boot_mean = np.mean(a=boot_samples)  # overall mean
boot_means = np.mean(a=boot_samples, axis=1)  # mean of each bootstrap sample
boot_mean

# sample from normal distribution
norm_dist = normal_from_exp(
    lamb=LAMBDA,
    n_samples=n_samples,
    n_reps=n_large,
)
df = pd.DataFrame({"boot":boot_means, "normal_distribution": norm_dist})
boot_means.shape, norm_dist.shape

((10000,), (10000,))

In [21]:
fig = px.histogram(df, barmode="overlay", opacity=0.3)
fig.add_vline(
    x=boot_mean,
    annotation_text="Bootstrap mean",
    annotation_position="top left",
    annotation_font_size=15,
    annotation_font_color="blue",
)
fig.add_vline(
    x=1/LAMBDA,
    annotation_text="Expectation of normal distribution",
    annotation_position="top right",
    annotation_font_size=15,
    annotation_font_color="red",
)
fig.show()

The two distributions are fairly close for large number of samples.

In [22]:
store_boot_mean = []
n_large_vals = [2**k for k in range(20)]
for n_large in n_large_vals:
    # Compute mean of bootstrap samples
    boot_samples = boot_from_exp(lamb=LAMBDA, n_samples=n_samples, n_reps=n_large)
    boot_mean = np.mean(a=boot_samples)  # overall mean
    store_boot_mean.append(boot_mean)
store_boot_mean = np.array(store_boot_mean)

In [23]:
df = pd.DataFrame({"boot mean": np.abs((1/LAMBDA) - store_boot_mean), "value of n_large": n_large_vals})
px.line(df, x="value of n_large", y="boot mean", log_x=True, title="l1-norm to 1/lambda")

We see a clear decreasing trend as we increase the number of samples on which we perform bootstraps. This means that the we get closer and closer to $\frac{1}{\lambda}$ as we increase `n_large`. This is a practical illustration of the Central Limit Theorem.